## Lecture 22: PDEs1 
### Phys 503, J.R. Gladden, University of Mississippi

### Partial Differential Equations
Partial differential equations mathematically describe a system which depends on multiple variables and their derivatives. Examples are:
- Wave equation (acoustics, optics)
- Laplace equation (electrostatics)
- Schrodinger equation (quantum mechanics)
- Navier-Stokes equation (fluid flow)


An example of a typical 2nd order PDE would be the 2D Laplace equation for the electrostatic potential (more on this in Lecture 22):
$$ \mu \left( \frac{\partial^2 \Phi}{\partial x^2} + \frac{\partial^2 \Phi}{\partial y^2} \right)=0 $$

A another classic example is the time evolution of the 1D wave equation:
$$  \frac{\partial^2 \Psi}{\partial t^2} = c^2 \frac{\partial^2 \Psi}{\partial x^2} $$

### The Solver
This solver supplies both vector and scalar approaches to solving the 1D wave equation. Imports first...

In [14]:
%matplotlib wx
import numpy as np
import matplotlib.pyplot as plt
import time
import matplotlib.animation as animation

In [9]:
def solver0(I,f,c,L,n,dx,tstop,dt=0.0,method='v'):
    '''
	Wave equation solver.
	JRG, April 2014
	Input:
		I - callable initial condition function 
		f - callable forcing function
		c - wavespeed
		L - length of domain
		n - number of space steps
		dx- space step
		tstop - stop time (assume start at t=0.0)
		dt - set to 0.0 to allow program to choose time step
		method - (v)ector or (s)calar.
	Output:
		- computed dt [float]
		- fullU (solution at all time steps) [list of arrays]
		- method used [string]
    '''
	
	#Set up an empty list container for solutions at ALL time steps
    fullU=[]
    #if dt is not specified, make largest that is stable
    
    if dt <= 0:  dt=dx/float(c)
#    print dt
    
    C2=(c*dt/dx)**2
    dt2=dt*dt
    
    up=np.zeros(n+1)		#solution array at t=t+dt
    u=up.copy()			# solution at t
    um=up.copy()		#solution at t-dt

    t=0.0
    
    #Set up intitial conditions
    for i in range(n+1):
        u[i]=I(x[i])
    for i in range(1,n):
        um[i]=u[i] + 0.5*C2*(u[i-1] - 2*u[i] + u[i+1]) + dt2*f(x[i],t)
    
    #Set up Dirichlet boundary conditions
    um[0]=0.
    um[n]=0.
    
    while t <= tstop:
        t_old = t; t+=dt
        if method == 's':
            for i in range(1,n):
                up[i] = -um[i] +2*u[i] + C2*(u[i-1] - 2*u[i] + u[i+1]) + dt2*f(x[i],t_old)
        elif method == 'v':
            up[1:n] = -um[1:n] +2*u[1:n] +C2*(u[0:n-1] - 2*u[1:n] +u[2:n+1]) + dt2*f(x[1:n],t_old)
        else:
            print "Method needs to be 's' for scalar or 'v' for vector.  \n Exiting ..."
            break
        up[0] = 0.; up[n] = 0.
        fullU.append(u)

        um=u.copy(); u=up.copy()
    return dt, fullU, method

### Visualization
Here we provide a dynamic animation and static waterfall options to visualize the wave evolution.

In [12]:
def animate(fullU):
	animFig=plt.figure()
	line,=plt.plot(x,fullU[0],'b-')
	speed=1.0*dt
	
	def init():
		line.set_ydata(np.zeros(len(x))+np.nan)
		plt.ylim([-1,1])
		plt.xlabel('X',fontsize=18)
		plt.ylabel('$\psi(x)$',fontsize=20)
		plt.title('Solution to the 1D Wave Equation')
		return line,
		
	def update(i): 
		line.set_ydata(fullU[i])
		time=float(i)*dt
		#text(max(x)*0.9,max(fullU[0])*0.9,'Time=%2.2f s'%time)
		ax=plt.axes()
		#txt=text(0.8,0.9,'Time=%2.2f s'%time,transform = ax.transAxes)
		return line, #, txt
		
	ani = animation.FuncAnimation(
		animFig,
		update,
		range(len(fullU)),
		blit=True,
		interval=20,
		init_func=init
		)
	plt.show()
	
def waterfallPlot(fullU,dstep=25,offsetFactor=0.5):
	numPlots=0
	offset=0.0
	for i in range(len(fullU)):
		if offset<max(fullU[i]): offset=offsetFactor*max(fullU[i])
		
	for step in range(0,len(fullU),dstep):
		time=float(step)*dt
		plt.plot(x,fullU[step]+numPlots*offset,label='t=%2.1f'%time)
		numPlots+=1
	
	plt.xlabel('X',fontsize=18)
	plt.ylabel('$\psi(x)$',fontsize=20)
	if numPlots<10: plt.legend()
	plt.show()

### Initial Conditions, Driving Forces, Main Program


In [16]:
# Set up initial condition (I) and a driver function (f)
def I(x): return 0.0# exp(-5*(x-L/3.)**2) #sin(2*pi*x/L)
def f(x,t): return  4.0*np.sin(2*np.pi*1*t+np.pi/4)*np.exp(-((x-L/3.5)*4)**2) 

n=400; tstop=10; L=10.
dx=L/float(n)
x=np.linspace(0,L,n+1)


t0=time.time()

dt,fullU,method=solver0(I,f,1.0,L,n,dx,tstop,dt=0.0,method='s')
tf=time.time()

print "Total time for method %s = %2.5f seconds." %(method,tf-t0) 

#waterfallPlot(fullU,offsetFactor=0.2, dstep=10)
animate(fullU)

Total time for method s = 0.86914 seconds.
